# Using TEBD for real time evolution by a nearest-neighbour Hamiltonian

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from tnsbasic.mps import MPS,MPO
import tnsbasic.contractor as contractor
import tnsbasic.operators as op
from tnsbasic.tebd import TEBD

plt.rcParams['figure.figsize'] = [12, 8];

# Pauli matrices, to construct spin operators

sigma0=np.identity(2);
sigmaX=np.array([[0,1.],[1.,0]]);
sigmaY=np.array([[0,-1j],[1j,0]]);
sigmaZ=np.array([[1.,0],[0,-1.]]);

# Single site basis states
vxPlus=(1./np.sqrt(2.))*np.array([1.,1.]); # |0>+|1>
vxMinus=(1./np.sqrt(2.))*np.array([1.,-1.]); # |0>-|1>

vyPlus=(1./np.sqrt(2.))*np.array([1.,1j]); # |0>+i|1>
vyMinus=(1./np.sqrt(2.))*np.array([1.,-1j]); # |0>-i|1>

vzPlus=np.array([1.,0.]); # |0>
vzMinus=np.array([0.,1.]); # |1>


In [ ]:
# Auxiliary function to compute the entropy given a vector of Schmidt values
def entropy(lambdas,cutoff=1E-10):
    # check they are normalized
    normL=np.sum(lambdas*lambdas);
    if abs(normL-1.)>1E-6:
        raise ValueError('Entropy expects a normalized vector of Schmidt values');
    validIdx=[i for i in range(len(lambdas)) if lambdas[i]>=cutoff];
    return -2*np.real(np.sum(lambdas[validIdx]**2*np.log(lambdas[validIdx])));
    

## Ising Hamiltonian

For our first example, we construct the two-body terms of the Ising Hamiltonian 
$$H=\sum_i J \sigma_z^{[i]} \sigma_z^{[i+1]}+g\sigma_x^{[i]}$$
We build a list of terms, and, for convenience, also write it as a MPO

In [ ]:
# Parameters of the problem
N=12;
d=2;

J=1.;
g=1.;

# A list of 2-body operators in the Hamiltonian (could be done with np.kron):
# leftmost term
hL=J*op.twoBodyOperator(sigmaZ,sigmaZ)+g*op.twoBodyOperator(sigmaX,sigma0)+(g/2)*op.twoBodyOperator(sigma0,sigmaX);
# bulk terms
h=J*op.twoBodyOperator(sigmaZ,sigmaZ)+(g/2)*op.twoBodyOperator(sigmaX,sigma0)+(g/2)*op.twoBodyOperator(sigma0,sigmaX);
# rightmost term
hR=J*op.twoBodyOperator(sigmaZ,sigmaZ)+(g/2)*op.twoBodyOperator(sigmaX,sigma0)+g*op.twoBodyOperator(sigma0,sigmaX);

# The whole list
H=[hL,*([h]*(N-3)),hR];

# The MPO form
Hmpo=MPO();
Hmpo.initializeFromNNterms(H,d);

## Global quench

We can initialize the system in a product state, and start evolving with our nearest neighbour Hamiltonian. 
We are interested in the expectation value of some observable during the evolution. 

[Running the algorithm](#running-the-algorithm)

Using the TEBD algorithm we can evolve the initial state and monitor the relevant expectation values. To do so, we
 
 1. initialize the state with ```MPS.initializeProductState(vector_list)```;
 
 2. initialize the TEBD algorithm with
 ```TEBD.initialize(d=2,D=10,N=10,order=1,delta=0.01,hamiltonian=None,cutoff=1E-10)```
where 
  - `order` is the Trotter order; supported are only first (1) or second (2)
  - `cutoff` is an optional argument that determines how Schmidt values are inverted (discarded if smaller than the cutoff);
  
 3. successively apply steps of time evolution using
 ```TEBD.runTimeEvolutionStep(state,delta=time_step,imaginaryTime=False,order=desired_order,D=desired_Dmax)```
where
  - `state` is a MPS on which the algorithm is applied (modified by the function)
  - `imaginaryTime=False` needs to be specified to ensure real time evolution (default is imaginary time),
  - the remaining parameters can be omitted (will take the values specified upon initialization).
 
 4. after running the function, the MPS `state` can be used to monitor the desired quantities.


In [ ]:
D=20;

# Initialize a product state
state=MPS();#N,d,D);
vSite=vxPlus;
v0=vSite;v0=np.reshape(vSite,[2,1,1]);
state.initializeProductState([v0]*N);
E0=np.real(contractor.contractBraMPOKet(state,Hmpo,state));
print('Energy of the initial state:',E0);


# We will be monitoring energy and expectation value of sigma_x at the N/2-th site 

# Decide on a Trotter order and time step
orderT=2;
delta=0.01;
totalT=5.5; # total time we want to evolve

# Initialize the algorithm
algorithm=TEBD();
state.canonicalForm();
algorithm.initialize(d,D,N,order=orderT,hamiltonian=H);
#algorithm.setTruncationScheme('zip');

#M=totalT//delta + (totalT%delta >0); # integer nr of steps

time=0.; # current time

# Initial values
Et=np.real(contractor.contractBraMPOKet(state,Hmpo,state));
evSx=np.real(contractor.localExpectationValue(state,sigmaX,N//2));   
entr=entropy(state.lambdas[N//2]);    
data=np.array([[time,Et,evSx,entr]]);

while time<totalT:
    algorithm.runTimeEvolutionStep(state,delta=delta,imaginaryTime=False,order=orderT,D=D,forceCanonical=False);
    state.canonicalForm(True);
    # Compute observable at the evolve state, and record results for plotting
    Et=np.real(contractor.contractBraMPOKet(state,Hmpo,state));
    evSx=np.real(contractor.localExpectationValue(state,sigmaX,N//2));   
    entr=entropy(state.lambdas[N//2]);    
    time+=delta;
    data=np.vstack([data,[time,Et,evSx,entr]]);
    #print('t=',time,', E=',np.real(Et),', Sx=',np.real(expSx),', S(N/2)=',entr);

In [ ]:
# Plot some results
plt.subplot(1,3,1);
f2=plt.plot(data[:,0],E0*np.ones([data.shape[0],1]),'k',label='initial energy');
f1=plt.plot(data[:,0],data[:,1],'b',label='D={0}'.format(D));
plt.xlabel('time');
plt.title('Energy');
plt.legend();

plt.subplot(1,3,2);
#f2=plt.plot(data[:,0],E0*np.ones([data.shape[0],1]),'k',label='initial energy');
f1=plt.plot(data[:,0],data[:,2],'b',label='D={0}'.format(D));
plt.xlabel('time');
plt.title(r'$\langle\sigma_x^{[N/2]}\rangle$');
#plt.legend();

plt.subplot(1,3,3);
#f2=plt.plot(data[:,0],E0*np.ones([data.shape[0],1]),'k',label='initial energy');
f1=plt.plot(data[:,0],data[:,3],'b',label='D={0}'.format(D));
plt.xlabel('time');
plt.title('Entropy');
#plt.legend();

## Convergence and errors

A fundamental issue when running these numerical simulations is that of convergence. In this algorithm we will have errors from the Trotter discretization and (mainly) from the truncation in bond dimension.

A useful quantity to monitor the evolution during such protocol as described above is the energy: since it is conserved during the evolution, deviations from its initial value flag a numerical error occurring.


## Exercises

1. How reliable are the results above regarding truncation error? Rerun cell `[8]` with a larger bond dimension and replot all results together (keep the data in a different array before rerunning). Repeat the exercise for a larger system, or different parameters.

2. **Local quench.** Combining imaginary and real time evolution, we can expore a different out-of-equilibrium scenario, in which the quench is only local. Starting from the ground state of the Hamiltonian $H$, apply a single site transformation (e.g. $\sigma_x$, notice this can be done with `MPS.applyLocalOperator(operator,site)`) and evolve with $H$. How does the entropy grow in this case?

3. **Quench from a ground state.** Instead of a product state, we can start the evolution from the ground state of a Hamiltonian $H_0(J_0,g_0)$, differing from $H$. 

